In [1]:
import sys
sys.path.append('../')

import pandas as pd
import numpy as np
import math
from timeit import default_timer as timer
from datetime import datetime, timedelta
import numba
from ensemble_processing import load_data, load, save

LABEL_COLUMN = "Future8WeekReturn"

/Users/neilkloot/anaconda/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
pd.options.display.max_rows=500
pd.options.display.max_columns=500

In [ ]:
# df1 = pd.read_pickle('../data/ml-20180512-processed.pkl.gz', compression='gzip')
# df2 = pd.read_pickle('../data/ml-20180512-labelled.pkl.gz', compression='gzip')
# df1 =  load_data('../data/ml-20180512-processed.pkl.gz', False)

df1 = load_data('../data/ml-20180512-processed.pkl.gz',
                               drop_unlabelled=False,
                               drop_labelled=True,
                               generate_labels=False,
                               label_weeks=8,
                               reference_date='2018-05-12')

In [ ]:
df1.columns.values

In [ ]:
# df1[['quoteDate_YEAR', 'quoteDate_MONTH', 'quoteDate_DAY']]
# pd.to_datetime(date_df)

In [ ]:
df2 = pd.read_csv('../data/symbol-industry-lookup.csv')

In [ ]:
df2

In [ ]:
len(df2['GICSIndustryGroup'].unique())

In [ ]:
len(df1)

In [ ]:
df3 = df1.merge(df2, left_on='symbol', right_on='symbol', how='left')
df3[df3['GICSSector'].isnull()]['symbol'].unique()

In [ ]:
df3

In [ ]:
from execute_xgboost_predictions import prepare_data_for_model

df_all_x, df_symbol_date = prepare_data_for_model(df1, False)

In [ ]:
df_symbol_date

In [ ]:
df_symbol_date.to_csv('test.csv')

In [ ]:
categories_df = pd.read_csv('../data/symbol-industry-lookup.csv')

In [ ]:
categories_df.head()

In [ ]:
train_model_names = load('../data/train_x_model_names.pkl.gz')
test_model_names = load('../data/test_x_model_names.pkl.gz')

In [ ]:
train_model_names

In [ ]:
train_model_names_df = pd.DataFrame({"symbol": train_model_names})

In [ ]:
train_model_names_df.head()

In [ ]:
test_model_names_df = pd.DataFrame({"symbol": test_model_names})

In [ ]:
all_df = pd.read_pickle('../data/ml-20180922-data.pkl.gz', compression='gzip')

In [4]:
all_df['lastTradePriceOnly'].isnull().sum()

11

In [16]:
all_df[all_df['lastTradePriceOnly']==1]

symbol  quoteDate  lastTradePriceOnly  adjustedPrice    volume  \
8139       CCA 2018-03-09                 1.0       1.000000     83254   
8178       CCA 2018-05-08                 1.0       1.000000    239719   
8619       IMF 2009-01-22                 1.0       0.510413    231300   
8621       IMF 2009-01-27                 1.0       0.525573    192500   
8627       IMF 2009-02-04                 1.0       0.492725    178200   
8639       IMF 2009-02-20                 1.0       0.528800    327500   
8643       IMF 2009-02-26                 1.0       0.507886    202000   
8648       IMF 2009-03-05                 1.0       0.505359     67700   
8649       IMF 2009-03-06                 1.0       0.528800     23000   
8654       IMF 2009-03-13                 1.0       0.528800    270400   
10401      IMF 2016-02-15                 1.0       0.830345    653400   
11248      REX 2008-03-31                 1.0       0.617226    538700   
11322      REX 2008-07-15                 1.0       0.593487     96400   
11387      REX 2008-10-17                 1.0       0.674000    113700   
11389      REX 2008-10-21                 1.0       0.599421     38700   
11393      REX 2008-10-27                 1.0       0.654263     75500   
11394      REX 2008-10-28                 1.0       0.654263     12500   
11395      REX 2008-10-29                 1.0       0.654263    104500   
11396      REX 2008-10-30                 1.0       0.654263    105500   
11397      REX 2008-10-31                 1.0       0.743000     15700   
11398      REX 2008-11-03                 1.0       0.654263    117500   
11399      REX 2008-11-04                 1.0       0.654263     27800   
11400      REX 2008-11-05                 1.0       0.654263     26600   
11401      REX 2008-11-06                 1.0       0.654263     80500   
11402      REX 2008-11-07                 1.0       0.743000     21300   
11403      REX 2008-11-10                 1.0       0.654263    179700   
11404      REX 2008-11-11                 1.0       0.654263     61000   
11405      REX 2008-11-12                 1.0       0.657534    180000   
11578      REX 2009-08-14                 1.0       0.654263    424800   
11770      REX 2010-05-28                 1.0       0.654263     69800   
11779      REX 2010-06-10                 1.0       0.654263     10600   
11793      REX 2010-07-02                 1.0       0.654263      5000   
11797      REX 2010-07-12                 1.0       0.654263     50000   
11954      REX 2011-03-15                 1.0       0.727039     28800   
11956      REX 2011-03-17                 1.0       0.716399     21800   
12069      REX 2011-09-05                 1.0       0.709306     39200   
12129      REX 2011-11-29                 1.0       0.787204     22500   
12130      REX 2011-11-30                 1.0       0.795076      3500   
12571      REX 2013-10-21                 1.0       0.880795     32000   
12572      REX 2013-10-22                 1.0       0.885199    122700   
12582      REX 2013-11-06                 1.0       0.880795    121000   
12585      REX 2013-11-13                 1.0       0.867583     36800   
12587      REX 2013-11-15                 1.0       1.000000     23100   
12797      REX 2014-10-23                 1.0       0.880795     29300   
12798      REX 2014-10-24                 1.0       1.000000       700   
12869      REX 2015-02-18                 1.0       0.924834     16000   
12875      REX 2015-02-26                 1.0       0.880795    102500   
12876      REX 2015-02-27                 1.0       1.000000      7900   
12879      REX 2015-03-04                 1.0       0.889603      5500   
12890      REX 2015-03-20                 1.0       1.000000      2500   
12891      REX 2015-03-23                 1.0       0.880795     62500   
12894      REX 2015-03-31                 1.0       0.880795     11000   
12895      REX 2015-04-02                 1.0       1.000000     10600   
12933      R

In [19]:
all_df[all_df['lastTradePriceOnly']==1].shape[0]

5848

In [20]:
all_df.loc[all_df['symbol'] == '1ST', :]

symbol  quoteDate  lastTradePriceOnly  adjustedPrice   volume  daysHigh  \
42276    1ST 2015-06-09             0.15725        0.15725  5217400   0.19768   
42277    1ST 2015-06-10             0.14377        0.14377  1598000   0.15275   
42278    1ST 2015-06-11             0.14377        0.14377  2093200   0.15275   
42279    1ST 2015-06-12             0.15275        0.15275   223700   0.15275   
42280    1ST 2015-06-15             0.14377        0.14377   318000   0.15275   
42281    1ST 2015-06-17             0.15275        0.15275   431200   0.15275   
42282    1ST 2015-06-18             0.14377        0.14377   541000   0.15275   
42283    1ST 2015-06-19             0.14377        0.14377    63900   0.14826   
42284    1ST 2015-06-22             0.12580        0.12580   312900   0.13928   
42285    1ST 2015-06-23             0.13029        0.13029   140100   0.13029   
42286    1ST 2015-06-24             0.13928        0.13928    18900   0.13928   
42287    1ST 2015-06-25             0.14377        0.14377    71100   0.14377   
42288    1ST 2015-06-29             0.11681        0.11681   479100   0.13928   
42289    1ST 2015-06-30             0.12130        0.12130   214600   0.13029   
42290    1ST 2015-07-02             0.12130        0.12130   491700   0.14377   
42291    1ST 2015-07-03             0.13478        0.13478   650100   0.13478   
42292    1ST 2015-07-06             0.13478        0.13478   210800   0.13478   
42293    1ST 2015-07-07             0.13029        0.13029   178500   0.13928   
42294    1ST 2015-07-08             0.13029        0.13029   100600   0.13029   
42295    1ST 2015-07-09             0.12580        0.12580   111200   0.13029   
42296    1ST 2015-07-10             0.12580        0.12580     5700   0.12580   
42297    1ST 2015-07-13             0.12580        0.12580   133500   0.12580   
42298    1ST 2015-07-14             0.11232        0.11232   691400   0.12580   
42299    1ST 2015-07-15             0.11232        0.11232   157700   0.11232   
42300    1ST 2015-07-16             0.10783        0.10783   296700   0.11232   
42301    1ST 2015-07-17             0.12130        0.12130    93100   0.12130   
42302    1ST 2015-07-20             0.11232        0.11232    12000   0.12130   
42303    1ST 2015-07-21             0.11232        0.11232   106800   0.11232   
42304    1ST 2015-07-22             0.11232        0.11232   227300   0.11232   
42305    1ST 2015-07-23             0.10783        0.10783   267400   0.11232   
42306    1ST 2015-07-24             0.10333        0.10333   209600   0.10783   
42307    1ST 2015-07-27             0.10783        0.10783    62800   0.10783   
42308    1ST 2015-07-28             0.10783        0.10783    75200   0.10783   
42309    1ST 2015-07-29             0.10783        0.10783     4600   0.10783   
42310    1ST 2015-07-30             0.11232        0.11232   241800   0.11232   
42311    1ST 2015-07-31             0.09884        0.09884    89000   0.09884   
42312    1ST 2015-08-03             0.11232        0.11232   784500   0.11681   
42313    1ST 2015-08-04             0.10783        0.10783   280400   0.11232   
42314    1ST 2015-08-05             0.13029        0.13029  1276700   0.13029   
42315    1ST 2015-08-06             0.13928        0.13928  1544500   0.15725   
42316    1ST 2015-08-07             0.13928        0.13928   475800   0.14826   
42317    1ST 2015-08-10             0.14377        0.14377   268400   0.14377   
42318    1ST 2015-08-11             0.13478        0.13478   188200   0.13928   
42319    1ST 2015-08-12             0.12580        0.12580   352200   0.13928   
42320    1ST 2015-08-13             0.11681        0.11681   234500   0.12130   
42321    1ST 2015-08-14             0.12580        0.12580    11100   0.12580   
42322    1ST 2015-08-17             0.11681        0.11681   188900   0.12130   
42323    1ST 2015-08-18             0.10783        0.10783   444500   0.11681   
42324    1ST 2015-08-19             0

In [21]:
from dateutil.parser import parse
print(parse('1ST'))

2018-09-01 00:00:00


In [ ]:
all_df = pd.read_pickle('../data/ml-20180922-data.pkl.gz', compression='gzip')
data_model_names_df = pd.DataFrame({"symbol": all_df['symbol'].unique()})
del all_df

processed_df = pd.read_pickle('../data/ml-20180922-processed.pkl.gz', compression='gzip')
processed_model_names_df = pd.DataFrame({"symbol": processed_df['symbol'].unique()})
del processed_df

labelled_df = pd.read_pickle('../data/ml-20180922-labelled.pkl.gz', compression='gzip')
labelled_df_model_names_df = pd.DataFrame({"symbol": labelled_df['symbol'].unique()})
del labelled_df

In [ ]:
data_model_names_df
data_model_names_df[data_model_names_df['symbol']=='NA']

In [ ]:
processed_model_names_df
processed_model_names_df[processed_model_names_df['symbol']=='NA']

In [ ]:
labelled_df_model_names_df

In [ ]:
def append_industry_categories(df: pd.DataFrame, catgories_df: pd.DataFrame):
    """
        Adds the industry categpry (GICS) values to the dataset by matching on symbol
    """

    print('Adding industry categories to data set')
    output_df = df.merge(catgories_df, left_on='symbol',
                         right_on='symbol', how='left')

    return output_df


In [ ]:
train_industry_cats_df = append_industry_categories(train_model_names_df, categories_df)

In [ ]:
train_industry_cats_df.head(5000)

In [ ]:
train_industry_cats_df.isnull().sum()

In [ ]:
train_industry_cats_df[train_industry_cats_df.isnull().any(axis=1)]

In [ ]:
train_industry_cats_df[train_industry_cats_df.isnull().any(axis=1)]['symbol'].unique()

In [ ]:
train_industry_cats_df.fillna('Unknown', inplace=True)

In [ ]:
test_industry_cats_df = append_industry_categories(test_model_names_df, categories_df)
test_industry_cats_df.fillna('Unknown', inplace=True)
test_industry_cats_df[train_industry_cats_df.isnull().any(axis=1)]['symbol'].unique()

In [ ]:
def convert_file_string(original_name):
    output_str = original_name.replace('&', 'And')
    output_str = output_str.replace(',', '')
    output_str = output_str.replace('-', '')
    output_str = output_str.replace('(', '')
    output_str = output_str.replace(')', '')
    output_str = output_str.replace(' ', '')
    return output_str


def fix_categorical(categorical_data):
    unique_vals = categorical_data.unique()
    category_renamer = {}

    for index, element in enumerate(unique_vals):
        category_renamer[element] = convert_file_string(element)

    print('Converting categories')
    print(category_renamer)

    return categorical_data.rename_categories(category_renamer)

In [ ]:
train_gics_sectors_opt = pd.DataFrame()
test_gics_sectors_opt = pd.DataFrame()

train_gics_sectors_opt['symbol'] = train_industry_cats_df['symbol']
train_gics_sectors_opt['GICSSector'] = train_industry_cats_df['GICSSector'].astype('category')
train_gics_sectors_opt['GICSIndustryGroup'] = train_industry_cats_df['GICSIndustryGroup'].astype('category')
train_gics_sectors_opt['GICSIndustry'] = train_industry_cats_df['GICSIndustry'].astype('category')

test_gics_sectors_opt['symbol'] = test_industry_cats_df['symbol']
test_gics_sectors_opt['GICSSector'] = test_industry_cats_df['GICSSector'].astype('category')
test_gics_sectors_opt['GICSIndustryGroup'] = test_industry_cats_df['GICSIndustryGroup'].astype('category')
test_gics_sectors_opt['GICSIndustry'] = test_industry_cats_df['GICSIndustry'].astype('category')

train_gics_sectors = train_gics_sectors_opt['GICSSector'].values
train_gics_industry_groups = train_gics_sectors_opt['GICSIndustryGroup'].values
train_gics_industries = train_gics_sectors_opt['GICSIndustry'].values

test_gics_sectors = test_gics_sectors_opt['GICSSector'].values
test_gics_industry_groups = test_gics_sectors_opt['GICSIndustryGroup'].values
test_gics_industries = test_gics_sectors_opt['GICSIndustry'].values

# Fix the names used in the GICS data - remove '&' ',' and ' '
train_gics_sectors = fix_categorical(train_gics_sectors)
train_gics_industry_groups = fix_categorical(
    train_gics_industry_groups)
train_gics_industries = fix_categorical(train_gics_industries)

test_gics_sectors = fix_categorical(test_gics_sectors)
test_gics_industry_groups = fix_categorical(test_gics_industry_groups)
test_gics_industries = fix_categorical(test_gics_industries)

save(train_gics_sectors, '../data/train_x_GICSSector.pkl.gz')
save(train_gics_industry_groups, '../data/train_x_GICSIndustryGroup.pkl.gz')
save(train_gics_industries, '../data/train_x_GICSIndustry.pkl.gz')

save(test_gics_sectors, '../data/test_x_GICSSector.pkl.gz')
save(test_gics_industry_groups, '../data/test_x_GICSIndustryGroup.pkl.gz')
save(test_gics_industries, '../data/test_x_GICSIndustry.pkl.gz')

In [ ]:
labelled_df = pd.read_pickle('../data/ml-20180922-labelled.pkl.gz', compression='gzip')

In [ ]:
labelled_df[labelled_df['future_eight_week_return_T1_40P'].isnull()]

In [ ]:
labelled_df['two_week_bollinger_prediction'].fillna('Steady').astype('category')

In [ ]:
labelled_df[labelled_df['symbol']=='NA'].shape[0]

In [ ]:
del labelled_df

In [ ]:
all_df = pd.read_pickle('../data/ml-20180922-data.pkl.gz', compression='gzip')

In [ ]:
all_df[all_df['symbol']=='NA']

In [ ]:
all_df = append_industry_categories(all_df, categories_df)

In [ ]:
all_df[all_df['symbol'].isnull()]